In [1]:
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np

from sklearn.model_selection import train_test_split
from sklearn.preprocessing import OneHotEncoder

from keras.layers import Input, Dense, Activation, TextVectorization, Embedding, GlobalAveragePooling1D
from keras.models import Model
import tensorflow as tf

# Vetorização e Embedding de textos

# Exercício 1
*Objetivo: entender como funciona a camada TextVectorization*

Quando usamos sklearn, temos os objetos do tipo *vectorizer* que transformam strings em matrizes, em formatos que são "compreensíveis" por uma máquina. Em Keras, vamos usar a camada do tipo `TextVectorization` para o mesmo fim.

No código abaixo:

1. O que significa `output_mode='multi_hot'`?
1. Como acessamos o vocabulário do vectorizer?
1. O que significa o valor em `y[0,2]`?
1. O que significa a palavra `[UNK]` no vocabulário do vectorizer?
1. Da forma que está, o vetorizador é equivalente a qual construção do sklearn?

In [3]:
toy_dataset = ["este é um texto", "outro texto este é", "outro texto só é peixe na virada da maré"]

text_vectorization = TextVectorization(output_mode='multi_hot')
text_vectorization.adapt(toy_dataset)
y = text_vectorization(toy_dataset)
print(y)
print(text_vectorization.get_vocabulary())

tf.Tensor(
[[0. 1. 1. 0. 1. 0. 1. 0. 0. 0. 0. 0.]
 [0. 1. 1. 1. 1. 0. 0. 0. 0. 0. 0. 0.]
 [0. 1. 1. 1. 0. 1. 0. 1. 1. 1. 1. 1.]], shape=(3, 12), dtype=float32)
['[UNK]', 'é', 'texto', 'outro', 'este', 'virada', 'um', 'só', 'peixe', 'na', 'maré', 'da']


# Exercício 2
*Objetivo: usar um vetorizador dentro do modelo de rede neural*

O código abaixo incorpora o vetorizador ao modelo da rede neural de forma semelhante que o CountVectorizer e o LogisticRegression se acoplavam em uma pipeline.

Em Keras, o vetorizador deve ser treinado em separado do restante da rede porque o treinamento do vetorizador é feito na CPU, ao passo que o restante da rede pode ser treinado na GPU.

Outro detalhe importante é que a conversão dos rótulos para one-hot encoding deve ser feita fora do modelo (os modelos do Sklearn fazem essa operação internamente).

No código abaixo:

1. Aumente o número de épocas de treinamento para 30 e verifique o accuracy no conjunto de teste
1. Modifique o `output_mode` do vetorizador para `count` e depois para `tf_idf`. Houve modificação no accuracy? 

In [22]:
df = pd.read_csv('datasets/IMDB Dataset.csv').sample(1000)
ohe = OneHotEncoder()
y_ohe = ohe.fit_transform(df['sentiment'].to_numpy().reshape((-1,1))).todense()
X_train, X_test, y_train, y_test = train_test_split(df['review'], y_ohe)

In [6]:
vocab_size = 1000
def multihot_softmax_model(vectorize_layer, vocab_size=vocab_size):
    input_layer = Input(shape=(1,), dtype=tf.string)
    x = input_layer
    x = vectorize_layer(x)
    x = Dense(2, name='classificador')(x)
    x = Activation('softmax')(x)
    return Model(input_layer, x)

vectorize_layer = TextVectorization(output_mode='multi_hot', max_tokens=vocab_size, pad_to_max_tokens=True)
vectorize_layer.adapt(X_train)
clf = multihot_softmax_model(vectorize_layer)
print(clf.summary())
clf.compile(loss='categorical_crossentropy', metrics=['accuracy'])
history = clf.fit(X_train, y_train, epochs=30, verbose=1) # validation_split=0.1
clf.evaluate(X_test, y_test)

Model: "model_1"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_2 (InputLayer)        [(None, 1)]               0         
                                                                 
 text_vectorization_3 (TextV  (None, 1000)             0         
 ectorization)                                                   
                                                                 
 classificador (Dense)       (None, 2)                 2002      
                                                                 
 activation_1 (Activation)   (None, 2)                 0         
                                                                 
Total params: 2,002
Trainable params: 2,002
Non-trainable params: 0
_________________________________________________________________
None
Epoch 1/30
1172/1172 [==============================] - 18s 15ms/step - loss: 0.4090 - accuracy: 0.8235
Epoch 2/30
117

[0.34361761808395386, 0.8544800281524658]

# Exercício 3
*Objetivo: usar embeddings para representar documentos*

Até o momento, estamos representando nossos documentos como sequências de *inteiros*, em que cada inteiro representa uma palavra:

In [13]:
toy_dataset = ["este é um texto", "outro texto este é", "outro texto só é peixe na virada da maré"]

text_vectorization = TextVectorization(output_mode='int', max_tokens=vocab_size, pad_to_max_tokens=True, output_sequence_length=10)
text_vectorization.adapt(toy_dataset)
y = text_vectorization(toy_dataset)
print(y)
print(text_vectorization.get_vocabulary())

tf.Tensor(
[[ 5  2  7  3  0  0  0  0  0  0]
 [ 4  3  5  2  0  0  0  0  0  0]
 [ 4  3  8  2  9 10  6 12 11  0]], shape=(3, 10), dtype=int64)
['', '[UNK]', 'é', 'texto', 'outro', 'este', 'virada', 'um', 'só', 'peixe', 'na', 'maré', 'da']


Experimente colocar frases com palavras desconhecidas no trecho abaixo:

In [14]:
print(text_vectorization(["este texto tem um monte de palavras desconhecidas e isso realmente confunde nosso vetorizador"]))

tf.Tensor([[5 3 1 7 1 1 1 1 1 1]], shape=(1, 10), dtype=int64)


Uma vantagem da representação como sequência de inteiros é que preservamos a ordem das palavras. Uma desvantagem é que essa representação não é tão fácil de classificar como as que estávamos usando até agora.

Uma solução para isso é mapear os inteiros para vetores - esses sim, num espaço vetorial fácil de classificar. Para isso, usamos uma camada chamada Embedding, que funciona exatamente como um dicionário:

In [23]:
emb = Embedding(vocab_size, 2)
y = text_vectorization(["texto de exemplo"])
print(y)
print(emb(y))

tf.Tensor([[3 1 1 0 0 0 0 0 0 0]], shape=(1, 10), dtype=int64)
tf.Tensor(
[[[ 0.00478233 -0.02215688]
  [ 0.02697987 -0.03279947]
  [ 0.02697987 -0.03279947]
  [-0.03892293 -0.01765386]
  [-0.03892293 -0.01765386]
  [-0.03892293 -0.01765386]
  [-0.03892293 -0.01765386]
  [-0.03892293 -0.01765386]
  [-0.03892293 -0.01765386]
  [-0.03892293 -0.01765386]]], shape=(1, 10, 2), dtype=float32)


Por fim, temos mais um problema: a camada de embedding nos dá um tensor de dimensão: (batch x tempo x dimensão do embedding). Porém, nossa rede neural só consegue classificar elementos de dimensão (batch x features). Uma solução que podemos adotar para isso é tirar a média ao longo do tempo de todos os vetores do embedding, usando a camada GlobalAveragePooling1D:

In [16]:
avg = GlobalAveragePooling1D()
print(avg(emb(y)))#fazendo a media de todos as palavras no espaco

tf.Tensor([[0.00371374 0.00643715]], shape=(1, 2), dtype=float32)


Mas, você deve estar se perguntando: isso não vai fazer com que a informação de tempo seja jogada fora?

Sim. Por enquanto, e só porque não sabemos lidar com o tempo *ainda*. Vamos usar a técnica atual para fazer um classificador e investigá-lo.

---

No código abaixo, encontre:

1. Qual é a dimensão do embedding realizado.
1. Quantos parâmetros existem na camada de classificação.
1. Qual é o desempenho da rede após o treinamento?
1. O que acontece se o parâmetro `output_sequence_length` for reduzido no vectorize_layer? 

batch = numero de texto
output_sequence_lenght = numero de palavras por texto

In [31]:
def avg_embedding_softmax_model(vectorize_layer, vocab_size=vocab_size, n_classes=2):
    input_layer = Input(shape=(1,), dtype=tf.string)
    x = input_layer
    x = vectorize_layer(x)
    x = Embedding(vocab_size, 2, name='projecao')(x)
    x = GlobalAveragePooling1D()(x)
    x = Dense(n_classes, name='classificador')(x)
    x = Activation('softmax')(x)
    return Model(input_layer, x)

vectorize_layer = TextVectorization(output_mode='int', max_tokens=vocab_size, pad_to_max_tokens=True, output_sequence_length=200)
vectorize_layer.adapt(X_train)
clf = avg_embedding_softmax_model(vectorize_layer, n_classes=3)
print(clf.summary())
clf.compile(loss='categorical_crossentropy', metrics=['accuracy'])
history = clf.fit(X_train, y_train, epochs=5, verbose=1) # validation_split=0.1
clf.evaluate(X_test, y_test)

Model: "model_5"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 input_6 (InputLayer)        [(None, 1)]               0         
                                                                 
 text_vectorization_8 (TextV  (None, 200)              0         
 ectorization)                                                   
                                                                 
 projecao (Embedding)        (None, 200, 2)            2000      
                                                                 
 global_average_pooling1d_4   (None, 2)                0         
 (GlobalAveragePooling1D)                                        
                                                                 
 classificador (Dense)       (None, 3)                 9         
                                                                 
 activation_5 (Activation)   (None, 3)                 0   

[1.0969312191009521, 0.49186256527900696]

## Exercício 4
*Objetivo: visualizar e analisar as dimensões de embeddings atingidas pelo classificador*

As projeções abaixo mostram a projeção (embedding) de cada palavra conforme foram atingidas pelo classificador.

1. Analisando as figuras, você diria que aumentar o número de dimensões do embedding poderia levar a um ganho de desempenho no classificador?
1. Analisando as figuras, você diria que é possível reduzir o número de dimensões do embedding para tornar nosso classificador ainda menor?

In [21]:
import plotly.express as px

# Visualização: onde foi parar cada palavra?
projecoes = clf.get_layer('projecao').get_weights()[0]
vocabulario = vectorize_layer.get_vocabulary()
y_pred_ohe = clf.predict(vocabulario)
y_pred = ohe.inverse_transform(y_pred_ohe).reshape( (-1,))
df = pd.DataFrame()
df['dim_1'] = projecoes[:,0]
df['dim_2'] = projecoes[:,1]
df['word'] = vocabulario
df['prediction'] = y_pred

px.scatter(df, x="dim_1", y="dim_2", color="prediction", hover_data=["word"], title="Onde foi cada palavra?", width=600, height=600)

32/32 [==============================] - 0s 4ms/step


ValueError: Mime type rendering requires nbformat>=4.2.0 but it is not installed

Figure({
    'data': [{'customdata': array([[''],
                                   ['[UNK]'],
                                   ['the'],
                                   ...,
                                   ['70s'],
                                   ['hardly'],
                                   ['dumb']], dtype=object),
              'hovertemplate': ('prediction=positive<br>dim_1=%' ... '{customdata[0]}<extra></extra>'),
              'legendgroup': 'positive',
              'marker': {'color': '#636efa', 'symbol': 'circle'},
              'mode': 'markers',
              'name': 'positive',
              'orientation': 'v',
              'showlegend': True,
              'type': 'scatter',
              'x': array([-0.00376105, -0.00410437,  0.05107163, ...,  0.12819378, -0.79779196,
                          -1.3810997 ], dtype=float32),
              'xaxis': 'x',
              'y': array([ 0.04888783, -0.09002475,  0.06367081, ...,  0.17205164, -0.78846663,
                          -1.4227726 ], dtype=float32),
              'yaxis': 'y'},
             {'customdata': array([['bad'],
                                   ['worst'],
                                   ['awful'],
                                   ['waste']], dtype=object),
              'hovertemplate': ('prediction=negative<br>dim_1=%' ... '{customdata[0]}<extra></extra>'),
              'legendgroup': 'negative',
              'marker': {'color': '#EF553B', 'symbol': 'circle'},
              'mode': 'markers',
              'name': 'negative',
              'orientation': 'v',
              'showlegend': True,
              'type': 'scatter',
              'x': array([-3.562445 , -4.07812  , -3.4594793, -3.6195664], dtype=float32),
              'xaxis': 'x',
              'y': array([-3.6087298, -4.0528145, -3.4552927, -3.5776896], dtype=float32),
              'yaxis': 'y'}],
    'layout': {'height': 600,
               'legend': {'title': {'text': 'prediction'}, 'tracegroupgap': 0},
               'template': '...',
               'title': {'text': 'Onde foi cada palavra?'},
               'width': 600,
               'xaxis': {'anchor': 'y', 'domain': [0.0, 1.0], 'title': {'text': 'dim_1'}},
               'yaxis': {'anchor': 'x', 'domain': [0.0, 1.0], 'title': {'text': 'dim_2'}}}
})

In [24]:
import plotly.express as px
df = pd.read_csv('embeddings_over_epochs.csv') # Gravei esse arquivo antecipadamente - demora muito para refazê-lo!
df.head()
df['prediction'][0] = 'positive' # Isso é definitivamente um hack. Sem isso, o plotly não vê o label 'positive' na primeira época, e começa a remover o label 'positive' dos plots subsequentes.

px.scatter(df, x="dim_1", y="dim_2", animation_frame="epoch", animation_group="word",
            color="prediction", hover_name="word", title="Training a 2D word embedding for sentiment analysis <br><sup>Where did each word go in the embedding space?</sup>",
          range_x=[-15,15], range_y=[-15,15],
          width=800, height=800
          )


/var/folders/t2/cdclp43n5qb28dv0c2rypgx40000gn/T/ipykernel_14488/512069868.py:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



ValueError: Mime type rendering requires nbformat>=4.2.0 but it is not installed

Figure({
    'data': [{'hovertemplate': ('<b>%{hovertext}</b><br><br>pre' ... '}<br>dim_2=%{y}<extra></extra>'),
              'hovertext': array([nan], dtype=object),
              'ids': array([nan], dtype=object),
              'legendgroup': 'positive',
              'marker': {'color': '#636efa', 'symbol': 'circle'},
              'mode': 'markers',
              'name': 'positive',
              'orientation': 'v',
              'showlegend': True,
              'type': 'scatter',
              'x': array([-0.03641273]),
              'xaxis': 'x',
              'y': array([0.00932432]),
              'yaxis': 'y'},
             {'hovertemplate': ('<b>%{hovertext}</b><br><br>pre' ... '}<br>dim_2=%{y}<extra></extra>'),
              'hovertext': array(['[UNK]', 'the', 'a', ..., 'missing', 'unlike', 'caught'], dtype=object),
              'ids': array(['[UNK]', 'the', 'a', ..., 'missing', 'unlike', 'caught'], dtype=object),
              'legendgroup': 'negative',
              'marker': {'color': '#EF553B', 'symbol': 'circle'},
              'mode': 'markers',
              'name': 'negative',
              'orientation': 'v',
              'showlegend': True,
              'type': 'scatter',
              'x': array([ 0.04297637, -0.03635552, -0.00382483, ..., -0.00612896, -0.03449046,
                          -0.001578  ]),
              'xaxis': 'x',
              'y': array([ 0.01800307, -0.03134994, -0.0228092 , ...,  0.03965371, -0.02895738,
                          -0.0055985 ]),
              'yaxis': 'y'}],
    'frames': [{'data': [{'hovertemplate': ('<b>%{hovertext}</b><br><br>pre' ... '}<br>dim_2=%{y}<extra></extra>'),
                          'hovertext': array([nan], dtype=object),
                          'ids': array([nan], dtype=object),
                          'legendgroup': 'positive',
                          'marker': {'color': '#636efa', 'symbol': 'circle'},
                          'mode': 'markers',
                          'name': 'positive',
                          'orientation': 'v',
                          'showlegend': True,
                          'type': 'scatter',
                          'x': array([-0.03641273]),
                          'xaxis': 'x',
                          'y': array([0.00932432]),
                          'yaxis': 'y'},
                         {'hovertemplate': ('<b>%{hovertext}</b><br><br>pre' ... '}<br>dim_2=%{y}<extra></extra>'),
                          'hovertext': array(['[UNK]', 'the', 'a', ..., 'missing', 'unlike', 'caught'], dtype=object),
                          'ids': array(['[UNK]', 'the', 'a', ..., 'missing', 'unlike', 'caught'], dtype=object),
                          'legendgroup': 'negative',
                          'marker': {'color': '#EF553B', 'symbol': 'circle'},
                          'mode': 'markers',
                          'name': 'negative',
                          'orientation': 'v',
                          'showlegend': True,
                          'type': 'scatter',
                          'x': array([ 0.04297637, -0.03635552, -0.00382483, ..., -0.00612896, -0.03449046,
                                      -0.001578  ]),
                          'xaxis': 'x',
                          'y': array([ 0.01800307, -0.03134994, -0.0228092 , ...,  0.03965371, -0.02895738,
                                      -0.0055985 ]),
                          'yaxis': 'y'}],
                'name': '0'},
               {'data': [{'hovertemplate': ('<b>%{hovertext}</b><br><br>pre' ... '}<br>dim_2=%{y}<extra></extra>'),
                          'hovertext': array([nan, '[UNK]', 'the', ..., 'missing', 'unlike', 'caught'], dtype=object),
                          'ids': array([nan, '[UNK]', 'the', ..., 'missing', 'unlike', 'caught'], dtype=object),
                          'legendgroup': 'positive',
                          'marker': {'color': '#636efa', 'symbol': 'circle'},
                          'mode': 'markers

# Exercício 5
*Objetivo: fazer um classificador de intenções*

O código abaixo carrega um dataset de frases e intenções voltado para fazer um chatbot. Depois disso, ele seleciona as N_INTENTS intenções com mais exemplos na base de dados, simplificando o problema de classificação.

Com base nesses dados e no que já vimos hoje:

1. Programe, treine e avalie um classificador de intenções para o chatbot usando a topologia que vimos hoje. No treinamento, aumente o número de épocas até que o erro no conjunto de *validação* fique estável.
1. Faça um plot do espaço de embeddings e verifique como as palavras se organizam nele.

In [25]:
TRAIN_URL = 'https://raw.githubusercontent.com/AmFamMLTeam/ACID/master/customer_training.csv'
TEST_URL = 'https://raw.githubusercontent.com/AmFamMLTeam/ACID/master/customer_testing.csv'
df_train = pd.read_csv(TRAIN_URL)
df_test = pd.read_csv(TEST_URL)
intent_count = df_train['INTENT_NAME'].value_counts()
N_INTENTS = 3
allowed_intents = intent_count[0:N_INTENTS].index
filter_train = df_train['INTENT_NAME'].isin(allowed_intents)
df_train_ = df_train[filter_train]
filter_test = df_test['INTENT_NAME'].isin(allowed_intents)
df_test_ = df_test[filter_test]
print(allowed_intents)

Index(['INFO_ADD_REMOVE_VEHICLE', 'INFO_LOGIN_ERROR', 'INFO_ERS'], dtype='object', name='INTENT_NAME')


In [26]:
ohe = OneHotEncoder()
y_train = ohe.fit_transform(df_train_['INTENT_NAME'].to_numpy().reshape((-1,1))).todense()
y_test = ohe.transform(df_test_['INTENT_NAME'].to_numpy().reshape((-1,1))).todense()
X_train = df_train_['UTTERANCES']
X_test = df_test_['UTTERANCES']

projecoes = clf.get_layer('projecao').get_weights()[0]
vocabulario = vectorize_layer.get_vocabulary()
y_pred_ohe = clf.predict(vocabulario)
y_pred = ohe.inverse_transform(y_pred_ohe).reshape( (-1,))

avg_embedding_softmax_model()
df = pd.DataFrame()
df['dim_1'] = projecoes[:,0]
df['dim_2'] = projecoes[:,1]
df['word'] = vocabulario
df['prediction'] = y_pred

32/32 [==============================] - 0s 9ms/step


ValueError: Shape of the passed X data is not correct. Expected 3 columns, got 2.